In [1]:
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:98% !important; }</style>"))
display(HTML("<style>.output_result { max-width:98% !important; }</style>"))


# Code

## Imports

In [2]:
import pandas as pd
import numpy as np
import datetime
from collections import Counter
from tqdm.notebook import tqdm
import nltk
from nltk.corpus import stopwords
from nltk.util import ngrams, bigrams, trigrams
import statistics as stat
import seaborn as sns
import re
from nltk.stem.wordnet import WordNetLemmatizer
import plotly.colors as colors
import dataframe_image as dfi

# Set default color palette
colors_plotly_default = colors.qualitative.Plotly

main_path_mac = '/Users/philippmetzger/Documents/GitHub/battery_patents/'
#main_path_ssd = '/Volumes/Samsung Portable SSD T3 Media/'
main_path_ssd = '/Volumes/T7/Julius SSD Fortsetzung/'

import sys
packages_path = main_path_mac+'/07 Packages'
sys.path.append(packages_path)

from helpers import (current_time_string,
                              image_saver,
                              country_labels_dict,
                              ctry_code_name_dict,
                              message,
                              numbers_dict)


## Read the whole dataset and reduce it to what we are interested in

In [3]:
# Read the whole dataset
dataset_name = 'data_batteries_2022-01-26_1852'

path = main_path_ssd+'Dataset saves/04 From 15 Nov 2021 (release of 2021 Autumn edition)/01 Preprocessed/03 final - technologies tagged/'+dataset_name+'.csv'

print('Loading data from:')
print(path)

data = pd.read_csv(path, delimiter = ";", low_memory = False, na_values=['', ' ', '  '], keep_default_na = False)

print('Number of rows:', len(data))

print('Distinct values in column "granted":', pd.unique(data['granted']))

# Reduce it to non active parts, electrodes, secondary cells, charging, redox flow, and Nickel-Hydrogen
a = (data['non_active_parts_electrodes_secondary_cells'] == 1)
b = (data['charging'] == 1)
c = (data['is_Redox flow'] == 1)
d = (data['is_Nickel–hydrogen'] == 1)

data_reduced = data[a | b | c | d].copy()
del data
data = data_reduced

# Futher reduce it to IPFs only
data_ipf = data[data['tag'] == 'IPF'].copy()
ipf_percentage = (len(set(data_ipf['docdb_family_id'])) / len(set(data['docdb_family_id']))) * 100
print('Percentage of IPFs in relation to all battery patent families:'+str(round(ipf_percentage, 2))+'%')
del data
data = data_ipf


Loading data from:
/Volumes/T7/Julius SSD Fortsetzung/Dataset saves/04 From 15 Nov 2021 (release of 2021 Autumn edition)/01 Preprocessed/03 final - technologies tagged/data_batteries_2022-01-26_1852.csv
Number of rows: 4086532
Distinct values in column "granted": ['N' 'Y']
Percentage of IPFs in relation to all battery patent families:19.41%


## Sort it by ['dobdb_family_id', 'earliest_publn_date']

In [4]:
data = data.sort_values(by = ['docdb_family_id', 'earliest_publn_date'])


## Reduce to years we are interested in

In [5]:
print(set(data['earliest_publn_year_this_family_id']))


{1999, 2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019}


In [6]:
data_reduced = data[data['earliest_publn_year_this_family_id'] >= 2000].copy()
del data
data = data_reduced


In [7]:
print(set(data['earliest_publn_year_this_family_id']))


{2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019}


In [8]:
only_granted = False


## In appln_abstract and appln_title: Replace NaNs with '  '

In [9]:
data['appln_abstract'].fillna('  ', inplace=True)
data['appln_title'].fillna('  ', inplace=True)


## Infer our time frame from data

In [10]:
year_begin = min(data['earliest_publn_year_this_family_id'])
year_end = max(data['earliest_publn_year_this_family_id'])

years = list(range(year_begin, year_end + 1))
print(years)


[2000, 2001, 2002, 2003, 2004, 2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015, 2016, 2017, 2018, 2019]


## Of every family, keep only the last english, non-nan title and abstract

In [11]:
family_ids = pd.unique(data['docdb_family_id'])

# Create two dictionaries containing an empty set for each year
titles_dict = {}
abstracts_dict = {} 
for year in years:
    
    titles_dict[year] = set()
    abstracts_dict[year] = set()
    
for family_id in tqdm(family_ids):
    
    data_this_family_id = data[data['docdb_family_id']==family_id]
    
    earliest_publn_year_this_family_id = list(set(data_this_family_id['earliest_publn_year_this_family_id']))[0]
    
    
    # Get titles
    
    titles_this_family_id = list(pd.unique(data_this_family_id[
        data_this_family_id['appln_title_lg']=='en'
    ]['appln_title']))
    try:
        titles_this_family_id.remove('  ')
    except:
        pass
    
    try:
        last_title_this_family_id = titles_this_family_id[-1]
    except:
        pass
    
    titles_dict[earliest_publn_year_this_family_id].add(last_title_this_family_id)
    
    
    # Get abstracts
    
    abstracts_this_family_id = list(pd.unique(data_this_family_id[
        data_this_family_id['appln_abstract_lg']=='en'
    ]['appln_abstract']))
    try:
        abstracts_this_family_id.remove('  ')
    except:
        pass
    
    try:
        last_abstract_this_family_id = abstracts_this_family_id[-1]
    except:
        pass
    
    abstracts_dict[earliest_publn_year_this_family_id].add(last_abstract_this_family_id)
    

  0%|          | 0/92700 [00:00<?, ?it/s]

In [ ]:
family_ids = pd.unique(data['docdb_family_id'])

# Create two dictionaries containing an empty set for each year
titles_dict = {}
abstracts_dict = {} 
for year in years:
    
    titles_dict[year] = set()
    abstracts_dict[year] = set()
    
for family_id in tqdm(family_ids):
    
    data_this_family_id = data[data['docdb_family_id']==family_id]
    
    earliest_publn_year_this_family_id = list(set(data_this_family_id['earliest_publn_year_this_family_id']))[0]
    
    
    # Get titles
    
    titles_this_family_id = list(pd.unique(data_this_family_id[
        data_this_family_id['appln_title_lg']=='en'
    ]['appln_title']))
    try:
        titles_this_family_id.remove('  ')
    except:
        pass
    
    try:
        last_title_this_family_id = titles_this_family_id[-1]
    except:
        pass
    
    titles_dict[earliest_publn_year_this_family_id].add(last_title_this_family_id)
    
    
    # Get abstracts
    
    abstracts_this_family_id = list(pd.unique(data_this_family_id[
        data_this_family_id['appln_abstract_lg']=='en'
    ]['appln_abstract']))
    try:
        abstracts_this_family_id.remove('  ')
    except:
        pass
    
    try:
        last_abstract_this_family_id = abstracts_this_family_id[-1]
    except:
        pass
    
    abstracts_dict[earliest_publn_year_this_family_id].add(last_abstract_this_family_id)
    

## For Bruno: Of every family, keep only the last english, non-nan title and abstract and also save the respective family ID and year

In [69]:
family_ids = pd.unique(data['docdb_family_id'])

# Create two dictionaries containing an empty set for each year
titles_dict_bruno = {}
abstracts_dict_bruno = {} 
for family_id in family_ids:
    
    titles_dict_bruno[family_id] = tuple()
    abstracts_dict_bruno[family_id] = tuple()
    
for family_id in tqdm(family_ids):
    
    data_this_family_id = data[data['docdb_family_id']==family_id]
    
    earliest_publn_year_this_family_id = list(set(data_this_family_id['earliest_publn_year_this_family_id']))[0]
    
    
    # Get titles
    
    titles_this_family_id = list(pd.unique(data_this_family_id[
        data_this_family_id['appln_title_lg']=='en'
    ]['appln_title']))
    try:
        titles_this_family_id.remove('  ')
    except:
        pass
    
    try:
        last_title_this_family_id = titles_this_family_id[-1]
    except:
        pass
    
    titles_dict_bruno[family_id] = (earliest_publn_year_this_family_id, last_title_this_family_id)
    
    
    # Get abstracts
    
    abstracts_this_family_id = list(pd.unique(data_this_family_id[
        data_this_family_id['appln_abstract_lg']=='en'
    ]['appln_abstract']))
    try:
        abstracts_this_family_id.remove('  ')
    except:
        pass
    
    try:
        last_abstract_this_family_id = abstracts_this_family_id[-1]
    except:
        pass
    
    abstracts_dict_bruno[family_id] = (earliest_publn_year_this_family_id, last_abstract_this_family_id)
    

  0%|          | 0/92700 [00:00<?, ?it/s]

In [71]:
# Unfold abstracts_dict_bruno into a dataframe

df_bruno = pd.DataFrame.from_dict(abstracts_dict_bruno, orient='index', columns = ['earliest_publn_year_this_family_id', 'most_recent_abstract_this_family_id'])


In [73]:
# Make the index (family IDs) a column

df_bruno.reset_index(inplace=True)
df_bruno = df_bruno.rename(columns = {'index': 'family_id'})


In [74]:
df_bruno


family_id  earliest_publn_year_this_family_id  \
0        1574492                                2015   
1        3511554                                2000   
2        3613974                                2002   
3        3673165                                2002   
4        3681483                                2001   
...          ...                                 ...   
92695   73455420                                2019   
92696   73474213                                2015   
92697   74557388                                2015   
92698   74844536                                2004   
92699   74871121                                2019   

                     most_recent_abstract_this_family_id  
0      An underwater vehicle includes an on board pow...  
1      The method involves placing all loads (7,8,9,1...  
2      The electrode for an electrochemical arrangeme...  
3      The invention describes a method of regulating...  
4      The invention relates to an essentially flat e...  
...                                                  ...  
92695  The present invention provides a storage syste...  
92696  PROBLEM TO BE SOLVED: To provide a method allo...  
92697  A surgical instrument can comprise a handle, a...  
92698  FIELD: electrical engineering, namely manufact...  
92699  A Non-Linear Voltammetry (NLV)-based method fo...  

[92700 rows x 3 columns]

In [76]:
df_bruno.to_csv('ready_to_eat_bruno.csv', index = False)


## Get titles and abstracts counts for each year

In [12]:
titles_counts = []
for year in list(titles_dict):
    titles_counts.append(len(titles_dict[year]))

print(titles_counts)


[939, 1135, 1105, 1151, 1243, 1501, 1818, 2002, 2298, 2627, 3126, 4622, 5970, 6614, 7040, 6929, 6968, 7562, 8513, 9523]


In [13]:
abstracts_counts = []
for year in list(abstracts_dict):
    abstracts_counts.append(len(abstracts_dict[year]))

print(abstracts_counts)


[975, 1164, 1132, 1191, 1288, 1566, 1955, 2147, 2480, 2808, 3376, 5152, 6757, 7463, 7936, 7733, 7830, 8438, 9677, 11016]


In [227]:
sum(abstracts_counts)


92084

## Write counts in a dataframe and normalise them

In [14]:
# Read total yearly counts and add column 'normalised' 

#total_yearly_counts_df = pd.read_csv('/Users/philippmetzger/Documents/GitHub/MA_temp/03 Analysis/01 Country counts/total_yearly_counts', delimiter=';')
#total_yearly_counts_df.rename(columns = {'count': 'patent families count'}, inplace = True)

#max_patent_count = total_yearly_counts_df['patent families count'].max()
#total_yearly_counts_df['patent families count normalised'] = total_yearly_counts_df['patent families count'] / max_patent_count

total_yearly_counts_df = pd.DataFrame()

total_yearly_counts_df['titles counts'] = titles_counts
#max_titles_count = total_yearly_counts_df['titles counts'].max()
#total_yearly_counts_df['titles count normalised'] = total_yearly_counts_df['titles counts'] / max_titles_count


total_yearly_counts_df['abstracts counts'] = abstracts_counts
#max_abstracts_count = total_yearly_counts_df['abstracts counts'].max()
#total_yearly_counts_df['abstracts count normalised'] = total_yearly_counts_df['abstracts counts'] / max_abstracts_count


total_yearly_counts_df


titles counts  abstracts counts
0             939               975
1            1135              1164
2            1105              1132
3            1151              1191
4            1243              1288
5            1501              1566
6            1818              1955
7            2002              2147
8            2298              2480
9            2627              2808
10           3126              3376
11           4622              5152
12           5970              6757
13           6614              7463
14           7040              7936
15           6929              7733
16           6968              7830
17           7562              8438
18           8513              9677
19           9523             11016

## Define stopwords, contexts, equivalents, words to replace, and punctuation

In [315]:
stopwords_ = stopwords.words('english')
stopwords_.extend([
    'thereof', 'therefor', 'thereafter', 'wherein', 'utmost',
    'without', 'within',
    'xo', 'e', 'etc', 'ab', 'b', 'c', 'pct', 'wo', 'pt', 'pts', 'wt', 'xii', 'xiii', 'ymyo', 'xmn', 'xiv', 'le', 'sub',
    'r', 'x', 'g', 'p', 'v', 'zfz', 'zsz', 'z', 'f',
    'positive', 'negative', 'left', 'right',
    'high', 'low',
    'less', 'les', 'more', 'least',
    'judging', 'preparing', 'producing', 'comprising', 'following', 'containing', 'including', 'using', 'consisting',
    'making',
    'one', 'two', 'never',
    'end',
    'almost', 'like', 'also',
    'especially', 'preferably', 'surely', 'nearly', 'previously', 'mainly',
    'involves', 'comprises', 'provides', 'relates', 'belongs', 'discloses', 'includes',
    'solved', 'expressed', 'specified', 'provided', 'selected', 'characterized', 'included', 'equipped',
    'decided', 'made', 'filed', 'used', 'formed', 'said',
    'provide', 'improve', 'prevent', 'obtain', 'reduce', 'enhance', 'increase', 'suppress', 'realize', 'use',
    'first', 'second',
    'simple', 'convenient',
    'whose',
    'according',
    'capable', 'preferable', 'desirable', 'good',
    'desirably',
    'kind',
    'date', 'temp', 'sec', 
    'jan', 'apr', 'may', 'jun', 'jul', 'nov', 'oct',
    'jp',
    'problem', 'drawing', 'figure', 'invention', 'model', 'publication', 'utility', 'preparation',
    'method', 'application', 'purpose', 'number',
    'new', 'novel',
    'excellent',
    'non',
    'top', 'bottom'
])


# Contexts in which first word should be kept
contexts_after = [
    ['positive', 'electrode'],
    ['negative', 'electrode'],
    ['positive', 'electrodes'],
    ['negative', 'electrodes'],
    ['positive', 'active', 'material'],
    ['negative', 'active', 'material'],
    ['non', 'aqueous'],
    ['non', 'sintered'],
    ['top', 'cap'],
    ['bottom', 'plate']
]


# Contexts in which second word should be kept
contexts_before = [
    ['lithium', 'containing']
]
    

treat_as_same = [
    [('method', 'manufacturing'), ('manufacturing', 'method')],
    [('storage', 'battery', 'alkaline'), ('alkaline', 'storage', 'battery')],
    [('battery', 'alkaline', 'storage'), ('alkaline', 'storage', 'battery')]
]


replace_words = {
    'soln': 'solution',
    'aq': 'aqueous',
    'nonaqueous': 'non-aqueous',
    'obtd': 'obtained',
    'hr': 'hour',
    'pub': 'publication',
    'compsn': 'composition',
    'contg': 'containing',
    'compd': 'compound',
    'mfg': 'manufacturing',
    'methodfor': 'method for',
    'al': 'aluminium',
    'aluminum': 'aluminium',
    'co': 'cobalt',
    'mn': 'manganese',
    'ni': 'nickel',
    'zr': 'zirconium',
    'cr': 'chromium',
    'ti': 'titanium',
    'li': 'lithium',
    'la': 'lanthanum',
    'ce': 'cerium',
    'fe': 'iron',
    'ltoreq':'less than or equal',
    'deg': 'degree'
}


# This is not used in this application after all:
punctuation = '!"#$%&\()*+,-./:;<=>?@[\\]^_`{|}~'


In [316]:
# Check if replace_words dictionary works as it should

item = ['negative', 'obtd', 'soln', 'nonaqueous', 'active', 'material']

item_replaced = []
for word in item:
    
    if word in list(replace_words):
        
        item_replaced.extend(replace_words[word].split())
        
    else:
        
        item_replaced.append(word)
    
item = item_replaced
    
item


['negative', 'obtained', 'solution', 'non-aqueous', 'active', 'material']

## Define a function for taking care of key phrases extraction and counting

In [317]:
def growing_keywords(n_gram_length, item_type):
    
    # Initialise lemmatizer
    lem = WordNetLemmatizer()
    
    # create string for identifying the right language column
    #item_type_lg = item_type+'_lg'
    
    # Initialise n grams list
    ngrams_lists = []

    # Loop over years
    for year in tqdm(years):

        # Initialise n grams list for this year
        ngrams_list_this_year = []

        # Get all  
        #items_year = list(set(data[(data[item_type_lg]=='en') & (data['earliest_publn_year_this_family_id']==year)][item_type]))
        
        # Get this year's titles / abstracts (depending which mode we're in)
        if item_type == 'appln_title':
            items_year = list(titles_dict[year])
        if item_type == 'appln_abstract':
            items_year = list(abstracts_dict[year])
                
        for item in items_year:
            
            # Make all lowercase
            item = item.lower()

            # Punctuation removal
            item = re.sub('[^a-zA-Z]', ' ', item) 
            #for x in punctuation:
            #    item = item.replace(x,' ')

            # Tokenise
            item = item.split()
                        
            #####
            
            # 12 Oct 2022: Fixing the issue with "non aqueous" and "aqueous"
            
            #item_new = []
            
            aqueous_count = item.count('aqueous')
            
            #if aqueous_count>0:
            #    print(aqueous_count)
                
            for aqueous_occurrence in list(range(aqueous_count)):
                
                item_new = []
                
                #print(aqueous_occurrence)
            
                if 'aqueous' in item:
                    
                    #print('here')

                    aqueous_index = item.index('aqueous')
                    
                    #print(aqueous_index)
                    #print(item[aqueous_index])
                    
                    if aqueous_index>0:
                        
                        #print(aqueous_index - 1)
                        #print(item[aqueous_index - 1])
                        
                        if item[aqueous_index - 1] == 'non':
                            
                            #print('here')
                            
                            #print(item)
                            #print(len(item))

                            #for i, word in enumerate(item):
                            for word_index in list(range(len(item))):
                                
                                #print((i, word))
                                
                                #print(word_index)
                                #print(item[word_index])

                                if (word_index != aqueous_index) & (word_index != aqueous_index - 1):

                                    item_new.append(item[word_index])

                                elif (word_index == (aqueous_index - 1)):

                                    item_new.append('non-aqueous')

                                else:
                                    pass

                            item_save = item
                            item = item_new
                
                #print(item_save)
                #print(item_new)
                #print()
                                
            #####
            
            # Replace certain words with others (according to replace_words dictionary defined above)
            item_replaced = []
            
            for word in item:

                if word in list(replace_words):
        
                    item_replaced.extend(replace_words[word].split())

                else:

                    item_replaced.append(word)

            item = item_replaced
            
            #####
            
            # Remove stopwords; but only if they are not in a context that indicates that they should be kept.
            # Such contexts are defined in cell above (contexts_after and contexts_before).
            
            item_without_stopwords = []

            # For debugging: List of stopwords that will be checked
            check_list = []
            # For debugging: List of stopwords that are actually removed (because they are not in a certain context)
            remove_list = []
                        
            for i, word in enumerate(item):
                
                remove = False

                if word in stopwords_:
 
                    check_list.append(word)

                    # Treat cases with context after the word or phrase
        
                    in_context_after = False

                    for j, context in enumerate(contexts_after):
                        
                        if i<(len(item)-(len(context)-1)):

                            try:

                                to_compare = []
                                
                                for k in range(len(context)):
                                    to_compare.append(item[i+k])
                                    
                                if to_compare == context:
                                    in_context_after = True
                                    
                                    if False:
                                        print('not removed due to context')
                                        print(to_compare)
                                        print(context)
                                        print()

                            except:
                                print(contexts_after)
                                print(item)
                                print(len(item))
                                print(i+k)
                                print(to_compare)
                                print(context)

                    if not in_context_after:

                        remove = True
                        
                    # Treat cases with context before the word or phrase
        
                    in_context_before = False

                    for j, context in enumerate(contexts_before):
                        
                        if i>(len(context)-1):
                                
                            try:

                                to_compare = []

                                for k in range(len(context)):
                                    
                                    to_compare.append(item[i+k-(len(context)-1)])

                                if to_compare == context:
                                    in_context_before = True
                                    
                                    if False:
                                        print('not removed due to context')
                                        print(to_compare)
                                        print(context)
                                        print()

                            except:
                                print(contexts_before)
                                print(item)
                                print(len(item))
                                print(i+k)
                                print(to_compare)
                                print(context)

                    if not in_context_before:

                        remove = True
                        
                if not remove:
                    
                    item_without_stopwords.append(word)
                    
                else:
                                            
                    remove_list.append(word)

            #####
            
            # Delete words that are a repetition of the word before
            
            # Always add the first word to next stage
            # If this list of words is empty, do nothing
            try:
                item_without_stopwords_and_repetitions = [item_without_stopwords[0]]
            except Exception as e:
                pass
                                    
            # Loop over the other words (the second and following) and add them to the next stage, if they are not 
            # a repetition of the word before
            for i in range(1, len(item_without_stopwords)):
                
                if (item_without_stopwords[i-1] != item_without_stopwords[i]):
                    
                    item_without_stopwords_and_repetitions.append(item_without_stopwords[i]) 
            
            #####
            
            # Lemmatisation
            item_without_stopwords_lemmatized = [lem.lemmatize(word) for word in item_without_stopwords_and_repetitions] 

            #####
            
            # Get ngrams
            ngrams_ = list(ngrams(item_without_stopwords_lemmatized, n_gram_length))
            
            # Treat certain pairs of n_grams as the same (defined in cell above (treat_as_same))
            for n_gram_treat_as_same in treat_as_same:
                
                while n_gram_treat_as_same[0] in ngrams_:
                    
                    ngrams_.remove(n_gram_treat_as_same[0])
                    ngrams_.append(n_gram_treat_as_same[1])

            # Add to list
            ngrams_list_this_year.extend(ngrams_)
            
        # For 3-grams: delete it if first word is equal to third word, e.g. battery pack battery
        if n_gram_length == 3:
            
            ngrams_list_this_year_reduced = []
            
            for item in ngrams_list_this_year:
                
                if not item[0] == item[2]:
                    
                    ngrams_list_this_year_reduced.append(item)
                    
            ngrams_list_this_year = ngrams_list_this_year_reduced

        ngrams_lists.append(ngrams_list_this_year)
        
    print('N-grams created')

    #####
    
    # Count n grams' appearances
    counter_list = []
    unique_keys = set()

    for list_ in ngrams_lists:

        counter = dict(Counter(list_).most_common())
        counter_list.append(counter)

        unique_keys = unique_keys.union(set(counter.keys()))
        
    print('N-grams counted')

    #####
    
    # NEW 17 Jan 2022: Delete all phrases that have at least one year where the counter is zero.
    # V2, same day: Delete all phrases that have more than 15 years where the counter is zero.
    if False:
        
        unique_keys_reduced = set()

        for key_ in unique_keys:

            has_zero = 0

            for counter in counter_list:

                if key_ not in counter:

                    has_zero += 1

            if has_zero > 15:

                for counter in counter_list:

                    try:
                        counter.pop(key_)
                    except Exception as pop_error:
                        pass
                        #print(type(pop_error))
                        #print(pop_error)
                        #print()

            else:

                unique_keys_reduced.add(key_)

        unique_keys = unique_keys_reduced
                
    #####
    
    # Create a count entry of 0 for n grams that is present in at least one year but not in other(s)
    for counter in counter_list:

        for key_ in unique_keys:

            if key_ not in counter:

                counter[key_] = 0

    #####      
    
    relative = False
    
    # NEW 10 Nov 2021: Increment all counts by 1 (in order to avoid division by 0 in growth calculation)
    # This is only necessary when using relative growth (see growth calcuation further down)
    if relative:
        
        for counter in counter_list:

            for key_ in counter:

                    counter[key_] = counter[key_] + 1
    
    def growing_keywords_sub(counter_list, unique_keys, scale):
    
        #####

        # NEW 10 Nov 2021: Scale by year's distinct title / abstract count
        # NEW 18 Jan 2022: Scale by year's distinct title / abstract count to make it "per 1000 titles / abstracts"

        if scale:

            if item_type == 'appln_title':
                #normalised_patent_counts = list(total_yearly_counts_df['titles count normalised'])
                patent_counts = list(total_yearly_counts_df['titles counts'])

            elif item_type == 'appln_abstract':
                #normalised_patent_counts = list(total_yearly_counts_df['abstracts count normalised'])
                patent_counts = list(total_yearly_counts_df['abstracts counts'])

            else:
                print('Item type not recognised')
                return

            for i, counter in enumerate(counter_list):

                #normalised_patent_count_this_year = normalised_patent_counts[i]
                patent_count_this_year = patent_counts[i]

                for key_ in counter:

                    #value_scaled = counter[key_] / normalised_patent_count_this_year
                    value_scaled = counter[key_] / patent_count_this_year * 1000
                    counter[key_] = value_scaled


        #####

        # Calculate increase over whole time span
        growth_dict = {}
        growth_dict_absolute = {}

        for key_ in unique_keys:

            growth_dict[key_] = counter_list[len(counter_list) - 1][key_] - counter_list[0][key_]

        print('Difference over whole timespan calculated')

        # Calculate sum of absolute differences year-over-year; absolute => Growing and shrinking are treated as the same
        for key_ in unique_keys:

            growth = []
            for i in range(len(counter_list)-1):

                if not relative:

                    # Growth as abs(x1 - x0)
                    growth.append(abs(counter_list[i+1][key_]-counter_list[i][key_]))

                else:

                    # Growth as abs(x1 / x0) - 1. Only works if x0 is not zero.
                    try:
                        growth.append(abs((counter_list[i+1][key_] / counter_list[i][key_]) - 1))
                    except:
                        print('error')

            try:
                growth_dict_absolute[key_] = sum(growth)
            except Exception as e2:
                print(type(e2))
                print(e2)

        print('Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated')

        #####
        #####

        # Prepare positive growth plot
        highest_growth = dict(sorted(growth_dict.items(), key=lambda x:x[1], reverse=True))
        top_30_growth = list(highest_growth)[:30]
        top_50_growth = list(highest_growth)[:50]

        growing_list = []
        growing_list.append(top_50_growth)

        #####

        counts_list = []

        #for key_ in top_30_growth:
        for key_ in top_50_growth:

            counts = []

            for counter in counter_list:

                counts.append(counter[key_])

            counts_list.append(counts)

        #####

        df_keyword_growth = pd.DataFrame(index=years)
        for i, ngram_ in enumerate(top_50_growth):

            ngram_string = ' '.join(ngram_)

            df_keyword_growth[ngram_string] = counts_list[i]

        df_keyword_growth = df_keyword_growth.transpose()

        # Round all values
        df_keyword_growth = df_keyword_growth.round()
        df_keyword_growth = df_keyword_growth.apply(pd.to_numeric, downcast='integer')
        
        growing_list.append(df_keyword_growth)

        #####

        cm = sns.light_palette((260, 75, 60), input="husl", as_cmap=True)

        plot_positive_growth = df_keyword_growth.style.background_gradient(cmap=cm, axis=1)
        
        # Display thousands with comma separation
        plot_positive_growth.format("{:,d}")

        growing_list.append(plot_positive_growth)

        print('Positive change plot created')

        #####
        #####

        # Prepare negative growth plot

        highest_growth = dict(sorted(growth_dict.items(), key=lambda x:x[1], reverse=False))
        top_30_growth = list(highest_growth)[:30]
        top_50_growth = list(highest_growth)[:50]

        shrinking_list = []
        shrinking_list.append(top_50_growth)

        #####

        counts_list = []

        for key_ in top_50_growth:

            counts = []

            for counter in counter_list:

                counts.append(counter[key_])

            counts_list.append(counts)

        #####

        df_keyword_growth = pd.DataFrame(index=years)
        for i, ngram_ in enumerate(top_50_growth):

            ngram_string = ' '.join(ngram_)

            df_keyword_growth[ngram_string] = counts_list[i]

        df_keyword_growth = df_keyword_growth.transpose()

        # Round all values
        df_keyword_growth = df_keyword_growth.round()
        df_keyword_growth = df_keyword_growth.apply(pd.to_numeric, downcast='integer')

        shrinking_list.append(df_keyword_growth)

        #####

        cm = sns.light_palette((260, 75, 60), input="husl", as_cmap=True)

        plot_negative_growth = df_keyword_growth.style.background_gradient(cmap=cm, axis=1)
        
        # Display thousands with comma separation
        plot_negative_growth.format("{:,d}")

        shrinking_list.append(plot_negative_growth)

        print('Negative change plot created')

        #####
        #####

        # Prepare absolute growth plot
        highest_growth = dict(sorted(growth_dict_absolute.items(), key=lambda x:x[1], reverse=True))
        top_30_growth = list(highest_growth)[:30]
        top_50_growth = list(highest_growth)[:50]

        absolute_growth_list = []
        absolute_growth_list.append(top_50_growth)

        #####

        counts_list = []

        #for key_ in top_30_growth:
        for key_ in top_50_growth:

            counts = []

            for counter in counter_list:

                counts.append(counter[key_])

            counts_list.append(counts)

        #####

        df_keyword_growth = pd.DataFrame(index=years)
        for i, ngram_ in enumerate(top_50_growth):

            ngram_string = ' '.join(ngram_)

            df_keyword_growth[ngram_string] = counts_list[i]

        df_keyword_growth = df_keyword_growth.transpose()

        # Round all values
        df_keyword_growth = df_keyword_growth.round()
        df_keyword_growth = df_keyword_growth.apply(pd.to_numeric, downcast='integer')

        absolute_growth_list.append(df_keyword_growth)        
        
        #####

        cm = sns.light_palette((260, 75, 60), input="husl", as_cmap=True)
        
        plot_absolute_growth = df_keyword_growth.style.background_gradient(cmap=cm, axis=1)
        
        # Display thousands with comma separation
        plot_absolute_growth.format("{:,d}")

        absolute_growth_list.append(plot_absolute_growth)

        print('Absolute change plot created')

        return growing_list, shrinking_list, absolute_growth_list
    
    growing_list, shrinking_list, absolute_growth_list = growing_keywords_sub(counter_list, unique_keys, False)
    growing_list_scaled, shrinking_list_scaled, absolute_growth_list_scaled = growing_keywords_sub(counter_list, unique_keys, True)
    
    return growing_list, shrinking_list, absolute_growth_list, growing_list_scaled, shrinking_list_scaled, absolute_growth_list_scaled


## Define a function for generating LaTeX code

In [318]:
def generate_latex_code(df):
    """This function takes a dataframe with n-gram counts as input and generates LaTeX code for creating a table with row-wise color gradients"""
    
    max_ = df.max(axis = 1)
    min_ = df.min(axis = 1)
    
    intensity = (df.subtract(min_, axis = 0)).divide((max_ - min_), axis = 0) * 100
    
    table_width = df.shape[1]
    table_height = df.shape[0]

    latex_code = '\\begin{tabularx}{\linewidth} {| >{\\raggedright\\arraybackslash}p{3.7cm}'

    for i in range(table_width):
        latex_code = latex_code+'| >{\\raggedleft\\arraybackslash}X '

    latex_code = latex_code+'| }\n'

    first_row = '\mc{} & '
    for year in years[:-1]:
        first_row = first_row + '\mc{'+str(year)+'} & '
    first_row = first_row + '\mc{'+str(years[-1])+'}'
    first_row = first_row+' \\\\'

    latex_code = latex_code+first_row+'\n\\hline\n\\hline'

    for i in range(table_height):
    #for i in range(3): # For testing purposes: Create only 3 rows

        intensity_this_phrase = list(intensity.loc[df.index[i]])

        this_row_code = df.index[i]+' & '
        for j in range(table_width):

            # Make text color white when cell color is darker
            if (intensity_this_phrase[j] >= 40):
                textcolor = 'white'
            else:
                textcolor = 'black'

            if j < (table_width - 1):
                this_row_code = this_row_code+'\\cellcolor{blue!'+str(intensity_this_phrase[j])+'!white}\\textcolor{'+textcolor+'}{'+str(df.iloc[i,j])+'} & '

            else:                        
                this_row_code = this_row_code+'\\cellcolor{blue!'+str(intensity_this_phrase[j])+'!white}\\textcolor{'+textcolor+'}{'+str(df.iloc[i,j])+'} \\\\'

        this_row_code = this_row_code+'\n\\hline'

        latex_code = latex_code+'\n'+this_row_code

    latex_code = latex_code+'\n\\end{tabularx}'

    print(latex_code)
    

## Two more definitions

In [319]:
# Define whether to use median or mean
#measure_function = stat.mean
#measure_function = stat.mean


# Results

## Titles

### Titles - unigrams

In [320]:
growing_list_title_1, shrinking_list_title_1, highest_abs_change_list_title_1, growing_list_title_1_scaled, shrinking_list_title_1_scaled, highest_abs_change_list_title_1_scaled = growing_keywords(
    1,
    'appln_title'
)


  0%|          | 0/20 [00:00<?, ?it/s]

N-grams created
N-grams counted
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created


In [321]:
growing_list_title_1[2]


In [322]:
growing_list_title_1_scaled[2]


In [323]:
shrinking_list_title_1[2]


In [324]:
shrinking_list_title_1_scaled[2]


In [325]:
highest_abs_change_list_title_1[2]


In [326]:
highest_abs_change_list_title_1_scaled[2]

### Titles - bigrams

In [327]:
growing_list_title_2, shrinking_list_title_2, highest_abs_change_list_title_2, growing_list_title_2_scaled, shrinking_list_title_2_scaled, highest_abs_change_list_title_2_scaled = growing_keywords(
    2,
    'appln_title'
)


  0%|          | 0/20 [00:00<?, ?it/s]

N-grams created
N-grams counted
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created


In [328]:
growing_list_title_2[2]


In [329]:
growing_list_title_2_scaled[2]


In [330]:
shrinking_list_title_2[2]


In [331]:
shrinking_list_title_2_scaled[2]

In [332]:
highest_abs_change_list_title_2[2]

In [333]:
highest_abs_change_list_title_2_scaled[2]

### Titles - trigrams

In [334]:
growing_list_title_3, shrinking_list_title_3, highest_abs_change_list_title_3, growing_list_title_3_scaled, shrinking_list_title_3_scaled, highest_abs_change_list_title_3_scaled = growing_keywords(
    3,
    'appln_title'
)


  0%|          | 0/20 [00:00<?, ?it/s]

N-grams created
N-grams counted
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created


In [335]:
growing_list_title_3[2]


In [336]:
growing_list_title_3_scaled[2]


In [337]:
shrinking_list_title_3[2]


In [338]:
shrinking_list_title_3_scaled[2]


In [339]:
highest_abs_change_list_title_3[2]


In [340]:
highest_abs_change_list_title_3_scaled[2]


## Abstracts

### Abstracts - unigrams

In [341]:
growing_list_abstract_1, shrinking_list_abstract_1, highest_abs_change_list_abstract_1, growing_list_abstract_1_scaled, shrinking_list_abstract_1_scaled, highest_abs_change_list_abstract_1_scaled = growing_keywords(
    1,
    'appln_abstract'
)


  0%|          | 0/20 [00:00<?, ?it/s]

N-grams created
N-grams counted
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created


In [342]:
growing_list_abstract_1[2]


In [343]:
growing_list_abstract_1_scaled[2]

In [344]:
shrinking_list_abstract_1[2]


In [345]:
shrinking_list_abstract_1_scaled[2]


In [346]:
highest_abs_change_list_abstract_1[2]


In [347]:
highest_abs_change_list_abstract_1_scaled[2]


### Abstracts - bigrams

In [348]:
growing_list_abstract_2, shrinking_list_abstract_2, highest_abs_change_list_abstract_2, growing_list_abstract_2_scaled, shrinking_list_abstract_2_scaled, highest_abs_change_list_abstract_2_scaled = growing_keywords(
    2,
    'appln_abstract'
)


  0%|          | 0/20 [00:00<?, ?it/s]

N-grams created
N-grams counted
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created


In [349]:
growing_list_abstract_2[2]


In [350]:
growing_list_abstract_2_scaled[2]

In [351]:
shrinking_list_abstract_2[2]


In [352]:
shrinking_list_abstract_2_scaled[2]


In [353]:
highest_abs_change_list_abstract_2[2]


In [354]:
highest_abs_change_list_abstract_2_scaled[2]


### Abstracts - trigrams

In [355]:
growing_list_abstract_3, shrinking_list_abstract_3, highest_abs_change_list_abstract_3, growing_list_abstract_3_scaled, shrinking_list_abstract_3_scaled, highest_abs_change_list_abstract_3_scaled = growing_keywords(
    3,
    'appln_abstract'
)


  0%|          | 0/20 [00:00<?, ?it/s]

N-grams created
N-grams counted
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created
Difference over whole timespan calculated
Sum of absolute differences (abs(count_year_i+1 - count_year_i)) calculated
Positive change plot created
Negative change plot created
Absolute change plot created


In [40]:
# Before fixing the 'aqueous' issue
growing_list_abstract_3[2]


In [277]:
# After attempting to fix the 'aqueous' issue
growing_list_abstract_3[2]


In [356]:
# After actully fixing the 'aqueous' issue
growing_list_abstract_3[2]


In [357]:
# Generate LaTeX code
generate_latex_code(growing_list_abstract_3[1])


\begin{tabularx}{\linewidth} {| >{\raggedright\arraybackslash}p{3.7cm}| >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | }
\mc{} & \mc{2000} & \mc{2001} & \mc{2002} & \mc{2003} & \mc{2004} & \mc{2005} & \mc{2006} & \mc{2007} & \mc{2008} & \mc{2009} & \mc{2010} & \mc{2011} & \mc{2012} & \mc{2013} & \mc{2014} & \mc{2015} & \mc{2016} & \mc{2017} & \mc{2018} & \mc{2019} \\
\hline
\hline
ele

In [358]:
# Export as PNG
#dfi.export(growing_list_abstract_3[2], 'growing_list_abstract_3.png')


In [43]:
# Before fixing the 'aqueous' issue
growing_list_abstract_3_scaled[2]


In [280]:
# After attempting to fix the 'aqueous' issue
growing_list_abstract_3_scaled[2]


In [359]:
# After actully fixing the 'aqueous' issue
growing_list_abstract_3_scaled[2]


In [360]:
# Generate LaTeX code
generate_latex_code(growing_list_abstract_3_scaled[1])


\begin{tabularx}{\linewidth} {| >{\raggedright\arraybackslash}p{3.7cm}| >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | }
\mc{} & \mc{2000} & \mc{2001} & \mc{2002} & \mc{2003} & \mc{2004} & \mc{2005} & \mc{2006} & \mc{2007} & \mc{2008} & \mc{2009} & \mc{2010} & \mc{2011} & \mc{2012} & \mc{2013} & \mc{2014} & \mc{2015} & \mc{2016} & \mc{2017} & \mc{2018} & \mc{2019} \\
\hline
\hline
ele

In [361]:
# Export as PNG
#dfi.export(growing_list_abstract_3_scaled[2], 'growing_list_abstract_3_scaled.png')


In [362]:
shrinking_list_abstract_3[2]


In [363]:
len(shrinking_list_abstract_3[1].index.values)


50

In [364]:
for item in shrinking_list_abstract_3[1].index.values:
    print(item)

hydrogen absorbing alloy
temperature detection section
charge storage device
absorbing alloy electrode
copyright jpo inpit
safety valve element
lithium secondary cell
battery safety valve
portable information terminal
absorbing alloy powder
hydrogen storage alloy
information storage device
battery storage casing
polarity type electrode
polarity type collector
bi directional switch
current detector detecting
double layer capacitor
rest period followed
cooling medium passage
signal processing section
lithium ion polymer
main anode body
metallic porous body
function predetermined time
voltage supply terminal
ion polymer battery
output voltage vout
power feed mean
conductive porous body
hydrogen generating system
voltage change rate
residual battery capacity
circuit controlling charging
lithium manganese oxide
anode body portion
large secondary battery
sintered cadmium electrode
solar array system
consumer usage recorder
anode extension portion
alkaline electrochemical cell
signaling devic

In [365]:
# Generate LaTeX code
generate_latex_code(shrinking_list_abstract_3[1])


\begin{tabularx}{\linewidth} {| >{\raggedright\arraybackslash}p{3.7cm}| >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | }
\mc{} & \mc{2000} & \mc{2001} & \mc{2002} & \mc{2003} & \mc{2004} & \mc{2005} & \mc{2006} & \mc{2007} & \mc{2008} & \mc{2009} & \mc{2010} & \mc{2011} & \mc{2012} & \mc{2013} & \mc{2014} & \mc{2015} & \mc{2016} & \mc{2017} & \mc{2018} & \mc{2019} \\
\hline
\hline
hyd

In [366]:
# Export as PNG
#dfi.export(shrinking_list_abstract_3[2], 'shrinking_list_abstract_3.png')


In [367]:
shrinking_list_abstract_3_scaled[2]


In [368]:
len(shrinking_list_abstract_3_scaled[1].index.values)


50

In [369]:
shrinking_list_abstract_3[1].index.values == shrinking_list_abstract_3_scaled[1].index.values

array([ True, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False, False, False, False, False,
       False, False, False, False, False])

In [370]:
for item in shrinking_list_abstract_3_scaled[1].index.values:
    print(item)
    

hydrogen absorbing alloy
lithium manganese oxide
lead acid battery
hydrogen storage alloy
external power source
charge discharge cycle
charge storage device
rechargeable lithium battery
alkaline storage battery
double layer capacitor
portable information terminal
temperature detection section
electric double layer
absorbing alloy electrode
copyright jpo inpit
lithium secondary cell
active material electrode
polyolefin microporous film
safety valve element
battery safety valve
cooling medium passage
predetermined time period
nickel metal hydride
absorbing alloy powder
information storage device
transition metal compound
alkaline secondary battery
charging control circuit
iron cobalt nickel
power supply controller
battery storage casing
polarity type electrode
polarity type collector
bi directional switch
current detector detecting
rest period followed
mobile phone battery
electric power converter
treated steel sheet
surface treated steel
electrical system battery
manganese iron cobalt
c

In [371]:
# Generate LaTeX code
generate_latex_code(shrinking_list_abstract_3_scaled[1])


\begin{tabularx}{\linewidth} {| >{\raggedright\arraybackslash}p{3.7cm}| >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | >{\raggedleft\arraybackslash}X | }
\mc{} & \mc{2000} & \mc{2001} & \mc{2002} & \mc{2003} & \mc{2004} & \mc{2005} & \mc{2006} & \mc{2007} & \mc{2008} & \mc{2009} & \mc{2010} & \mc{2011} & \mc{2012} & \mc{2013} & \mc{2014} & \mc{2015} & \mc{2016} & \mc{2017} & \mc{2018} & \mc{2019} \\
\hline
\hline
hyd

In [372]:
# Export as PNG
#dfi.export(shrinking_list_abstract_3_scaled[2], 'shrinking_list_abstract_3_scaled.png')


In [373]:
highest_abs_change_list_abstract_3[2]


In [374]:
highest_abs_change_list_abstract_3_scaled[2]


## Search certain patterns

In [123]:
beg_or_space = '( +|^)'
end_or_space = '( +|$)'

def search_for_string(string, remove_punctuation):
    
    def remove_punctuation(item):
        item = re.sub('[^a-zA-Z]', ' ', item)
        return item
    
    feature = 'appln_title'
    feature_lg = 'appln_title_lg'
    data_this = data[data[feature_lg]=='en']
    
    if remove_punctuation:
        result_titles = data_this[data_this[feature].map(lambda x: remove_punctuation(x)).str.contains(string, case=False)][['earliest_publn_year_this_family_id', 'docdb_family_id', feature]]
    else:
        result_titles = data_this[data_this[feature].str.contains(string, case=False)][['earliest_publn_year_this_family_id', 'docdb_family_id', feature]]
        
    feature = 'appln_abstract'
    feature_lg = 'appln_abstract_lg'
    data_this = data[data[feature_lg]=='en']
    
    if remove_punctuation:
        result_abstracts = data_this[data_this[feature].map(lambda x: remove_punctuation(x)).str.contains(string, case=False)][['earliest_publn_year_this_family_id', 'docdb_family_id', feature]]
    else:
        result_abstracts = data_this[data_this[feature].str.contains(string, case=False)][['earliest_publn_year_this_family_id', 'docdb_family_id', feature]]
        
    return [result_titles, result_abstracts]

def get_occurence_counts(result):

    dicts = []

    print_ = ['Titles:', 'Abstracts:']
    
    for i, item in enumerate(result):

        dict_ = {}

        for year in set(item['earliest_publn_year_this_family_id']):

            ids = set(item[item['earliest_publn_year_this_family_id'] == year]['docdb_family_id'])
            num_ids = len(ids)

            dict_[year] = [num_ids, ids]

        #dicts.append(dict_)
        print(print_[i])
        
        for year in list(dict_):
            print(str(year)+': '+str(dict_[year][0])+' '+str(dict_[year][1]))
        
        print()
            

In [79]:
circular_economy = search_for_string('circular economy', True)


In [124]:
get_occurence_counts(circular_economy)


Titles:

Abstracts:
2012: 1 {45424723}



In [44]:
artificial_intelligence = search_for_string('artificial intelligence', True) 


In [125]:
get_occurence_counts(artificial_intelligence)


Titles:
2019: 1 {68983016}

Abstracts:
2017: 1 {58273994}
2018: 1 {64395568}
2019: 13 {68534112, 68070945, 67775140, 67768556, 68068844, 67806895, 68381807, 68070962, 67950899, 66101653, 68101366, 61873658, 68067835}



In [87]:
AI = search_for_string(beg_or_space+'AI'+end_or_space, True)


/var/folders/c3/ddgk3fbs6w1gm4pg4tfj0d0r0000gn/T/ipykernel_24475/3860805238.py:15: UserWarning: This pattern has match groups. To actually get the groups, use str.extract.
  result_titles = data_this[data_this[feature].map(lambda x: remove_punctuation(x)).str.contains(string, case=False)][['earliest_publn_year_this_family_id', 'docdb_family_id', feature]]
/var/folders/c3/ddgk3fbs6w1gm4pg4tfj0d0r0000gn/T/ipykernel_24475/3860805238.py:24: UserWarning: This pattern has match groups. To actually get the groups, use str.extract.
  result_abstracts = data_this[data_this[feature].map(lambda x: remove_punctuation(x)).str.contains(string, case=False)][['earliest_publn_year_this_family_id', 'docdb_family_id', feature]]


In [134]:
AI[1]

earliest_publn_year_this_family_id  docdb_family_id  \
324300                                 2003         27762088   
324301                                 2003         27762088   
324302                                 2003         27762088   
324297                                 2003         27762088   
324298                                 2003         27762088   
...                                     ...              ...   
4053596                                2019         68692627   
4053597                                2019         68692627   
4053598                                2019         68692627   
4053599                                2019         68692627   
4053600                                2019         68692627   

                                            appln_abstract  
324300   Disclosed are new Ca, Mg and Ni-containing all...  
324301   Disclosed are new Ca, Mg and Ni-containing all...  
324302   Disclosed are new Ca, Mg and Ni-containing all...  
324297   Disclosed are new Ca, Mg and Ni-containing all...  
324298   Disclosed are new Ca, Mg and Ni-containing all...  
...                                                    ...  
4053596  A mobile robot and drone device configured to ...  
4053597  A mobile robot and drone device configured to ...  
4053598  A mobile robot and drone device configured to ...  
4053599  A mobile robot and drone device configured to ...  
4053600  A robot and drone game comprising an electroni...  

[508 rows x 3 columns]

In [140]:
list(set(AI[1]['appln_abstract']))[6]


'The invention relates to a piece of glass, in particular glass solder, comprising the following components in mol%: P2O5 37-50 mol%, in particular 39-48 mol%, AI2O3 0-14 mol%, in particular 2-12 mol%, B2O3 2-10 mol%, in particular 4-8 mol%, Na2O 0-30 mol%, in particular 0-20 mol%, M2O 0-20 mol%, in particular 12-20 mol%, wherein M can be K, Cs or Rb, Li2O 0-42 mol%, in particular 0-40 mol%, preferably 17-40 mol%, BaO 0-20 mol%, in particular 0-20 mol%, preferably 5-20 mol%, and Bi2O3 0-10 mol%, in particular 1-5 mol%, preferably 2-5 mol%.'

In [126]:
get_occurence_counts(AI)


Titles:

Abstracts:
2016: 4 {54849608, 54010916, 57197533, 57320740}
2017: 4 {56896520, 60784615, 58709628, 60159359}
2018: 2 {64454152, 60182650}
2019: 10 {68070945, 66542054, 67987686, 67768556, 67806895, 68692627, 65015668, 66101653, 67987641, 65723514}
2003: 1 {27762088}
2004: 2 {33490608, 30767881}
2007: 1 {38256395}
2008: 1 {40002286}
2009: 1 {40833651}
2010: 1 {42119831}
2011: 4 {44711897, 42139122, 44937546, 42562666}
2012: 5 {45993992, 45688430, 43901104, 46577617, 46456891}
2013: 8 {47553025, 47089058, 48873338, 47215535, 46147450, 49548859, 47471837, 48128254}
2014: 4 {49753250, 49620027, 51843901, 49301687}
2015: 5 {52991072, 54554597, 49667465, 49949946, 51383742}



In [89]:
industry_4_0 = search_for_string('industry 4.0', False)


In [127]:
get_occurence_counts(industry_4_0)


Titles:

Abstracts:



In [91]:
smart_city = search_for_string('smart city', True) 


In [128]:
get_occurence_counts(smart_city)


Titles:

Abstracts:
2016: 1 {55653399}
2017: 1 {57983369}
2018: 1 {63445648}

